In [261]:
print("ok")

ok


In [262]:
import pandas as pd
from evidently.dashboard import Dashboard
from evidently.dashboard.tabs import DataDriftTab, CatTargetDriftTab
from evidently.model_profile import Profile
from evidently.model_profile.sections import DataDriftProfileSection
from sklearn.model_selection import train_test_split
from evidently import ColumnMapping


In [263]:
data_url = "https://raw.githubusercontent.com/selva86/datasets/master/BostonHousing.csv"
boston_frame = pd.read_csv("Visadataset.csv")

In [264]:
boston_frame.head()

case_id continent education_of_employee has_job_experience  \
0  EZYV01      Asia           High School                  N   
1  EZYV02      Asia              Master's                  Y   
2  EZYV03      Asia            Bachelor's                  N   
3  EZYV04      Asia            Bachelor's                  N   
4  EZYV05    Africa              Master's                  Y   

  requires_job_training  no_of_employees  yr_of_estab region_of_employment  \
0                     N            14513         2007                 West   
1                     N             2412         2002            Northeast   
2                     Y            44444         2008                 West   
3                     N               98         1897                 West   
4                     N             1082         2005                South   

   prevailing_wage unit_of_wage full_time_position case_status  
0         592.2029         Hour                  Y      Denied  
1       83425.6500         Year                  Y   Certified  
2      122996.8600         Year                  Y      Denied  
3       83434.0300         Year                  Y      Denied  
4      149907.3900         Year                  Y   Certified

In [265]:
boston_frame.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25480 entries, 0 to 25479
Data columns (total 12 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   case_id                25480 non-null  object 
 1   continent              25480 non-null  object 
 2   education_of_employee  25480 non-null  object 
 3   has_job_experience     25480 non-null  object 
 4   requires_job_training  25480 non-null  object 
 5   no_of_employees        25480 non-null  int64  
 6   yr_of_estab            25480 non-null  int64  
 7   region_of_employment   25480 non-null  object 
 8   prevailing_wage        25480 non-null  float64
 9   unit_of_wage           25480 non-null  object 
 10  full_time_position     25480 non-null  object 
 11  case_status            25480 non-null  object 
dtypes: float64(1), int64(2), object(9)
memory usage: 2.3+ MB


In [266]:
boston_frame.describe()

no_of_employees   yr_of_estab  prevailing_wage
count     25480.000000  25480.000000     25480.000000
mean       5667.043210   1979.409929     74455.814592
std       22877.928848     42.366929     52815.942327
min         -26.000000   1800.000000         2.136700
25%        1022.000000   1976.000000     34015.480000
50%        2109.000000   1997.000000     70308.210000
75%        3504.000000   2005.000000    107735.512500
max      602069.000000   2016.000000    319210.270000

In [267]:
boston_frame.shape

(25480, 12)

In [268]:
#x_train, x_test = train_test_split(boston_frame, test_size=0.2, random_state=42)
X = boston_frame.drop('case_status', axis=1)
y = boston_frame['case_status']

x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

reference_df = x_train.copy()
reference_df["case_status"] = y_train.values

current_df = x_test.copy()
current_df["case_status"] = y_test.values




In [269]:
boston_frame[200:]

case_id continent education_of_employee has_job_experience  \
200      EZYV201      Asia             Doctorate                  Y   
201      EZYV202      Asia            Bachelor's                  Y   
202      EZYV203      Asia            Bachelor's                  Y   
203      EZYV204      Asia              Master's                  N   
204      EZYV205      Asia           High School                  Y   
...          ...       ...                   ...                ...   
25475  EZYV25476      Asia            Bachelor's                  Y   
25476  EZYV25477      Asia           High School                  Y   
25477  EZYV25478      Asia              Master's                  Y   
25478  EZYV25479      Asia              Master's                  Y   
25479  EZYV25480      Asia            Bachelor's                  Y   

      requires_job_training  no_of_employees  yr_of_estab  \
200                       N             3282         1979   
201                       N             1313         2002   
202                       N             3128         1999   
203                       N             4757         1981   
204                       N             2122         1859   
...                     ...              ...          ...   
25475                     Y             2601         2008   
25476                     N             3274         2006   
25477                     N             1121         1910   
25478                     Y             1918         1887   
25479                     N             3195         1960   

      region_of_employment  prevailing_wage unit_of_wage full_time_position  \
200                   West         74441.11         Year                  Y   
201                   West         99469.71         Year                  Y   
202                   West         31890.66         Year                  Y   
203                Midwest        167376.13         Year                  Y   
204                Midwest        130404.72         Year                  Y   
...                    ...              ...          ...                ...   
25475                South         77092.57         Year                  Y   
25476            Northeast        279174.79         Year                  Y   
25477                South        146298.85         Year                  N   
25478                 West         86154.77         Year                  Y   
25479              Midwest         70876.91         Year                  Y   

      case_status  
200     Certified  
201     Certified  
202     Certified  
203     Certified  
204     Certified  
...           ...  
25475   Certified  
25476   Certified  
25477   Certified  
25478   Certified  
25479   Certified  

[25280 rows x 12 columns]

In [ ]:
column_mapping = ColumnMapping(
    target="case_status",      # REQUIRED for CatTargetDriftTab
    prediction=None            # optional
)


In [272]:
boston_data_drift_dashboard =Dashboard(tabs=[DataDriftTab(), CatTargetDriftTab()])
#boston_data_drift_dashboard.calculate(boston_frame[:200],boston_frame[200:])
boston_data_drift_dashboard.calculate(reference_df, current_df,column_mapping=column_mapping)
boston_data_drift_dashboard.show()

In [273]:
boston_data_drift_dashboard.save("boston_data_drift_dashboard.html")

In [274]:
import numpy as np
import pandas as pd
from scipy.stats import ks_2samp


class DataDriftDetector:
    def __init__(
        self,
        reference_df,
        current_df,
        target_col="case_status",
        psi_threshold=0.2,
        ks_threshold=0.05
    ):
        self.reference_df = reference_df
        self.current_df = current_df
        self.target_col = target_col
        self.psi_threshold = psi_threshold
        self.ks_threshold = ks_threshold

    def _calculate_psi(self, expected, actual, buckets=10):
        expected = np.array(expected)
        actual = np.array(actual)

        breakpoints = np.percentile(
            expected, np.linspace(0, 100, buckets + 1)
        )

        expected_counts = np.histogram(expected, bins=breakpoints)[0] / len(expected)
        actual_counts = np.histogram(actual, bins=breakpoints)[0] / len(actual)

        psi = np.sum(
            (expected_counts - actual_counts)
            * np.log((expected_counts + 1e-6) / (actual_counts + 1e-6))
        )

        return psi

    def check_feature_drift(self):
        drift_report = []

        feature_cols = [
            col for col in self.reference_df.columns
            if col != self.target_col
        ]

        for col in feature_cols:
            ref = self.reference_df[col].dropna()
            cur = self.current_df[col].dropna()

            # 🔥 NUMERIC FEATURES ONLY
            if pd.api.types.is_numeric_dtype(ref):

                psi = self._calculate_psi(ref, cur)
                ks_stat, ks_p = ks_2samp(ref, cur)

                drift_report.append({
                    "feature": col,
                    "type": "numeric",
                    "psi": round(psi, 4),
                    "psi_drift": psi > self.psi_threshold,
                    "ks_pvalue": round(ks_p, 4),
                    "ks_drift": ks_p < self.ks_threshold
                })

            # 🟡 CATEGORICAL FEATURES
            else:
                ref_dist = ref.value_counts(normalize=True)
                cur_dist = cur.value_counts(normalize=True)

                drift_score = (ref_dist - cur_dist).abs().sum()

                drift_report.append({
                    "feature": col,
                    "type": "categorical",
                    "population_shift": round(drift_score, 4),
                    "drift": drift_score > 0.3
                })

        return pd.DataFrame(drift_report)

    def check_target_drift(self):
        ref = self.reference_df[self.target_col]
        cur = self.current_df[self.target_col]

        ref_dist = ref.value_counts(normalize=True)
        cur_dist = cur.value_counts(normalize=True)

        drift = (ref_dist - cur_dist).abs().sum()

        return {
            "target_drift_score": round(drift, 4),
            "drift_detected": drift > 0.2
        }

    def run(self, use_evidently=False):
        print("🔍 Checking Feature Drift...")
        feature_drift = self.check_feature_drift()

        print("🎯 Checking Target Drift...")
        target_drift = self.check_target_drift()

        return {
            "feature_drift": feature_drift,
            "target_drift": target_drift
        }


In [275]:
detector = DataDriftDetector(
    reference_df=reference_df,
    current_df=current_df,
    target_col="case_status"
)

result = detector.run()

result["feature_drift"]
result["target_drift"]


🔍 Checking Feature Drift...
🎯 Checking Target Drift...


{'target_drift_score': 0.0013, 'drift_detected': False}